# Goal: predict whether a loan will end up with maximum profits or not

---
#### Target variable: `zeroBalCode` 
* Type: **Categorical** 
* Model type: Classification 
* Sourced from: `zeroBalCode`
* Data: 
    - "0" means "Successful outcome for Fannie Mae"
    - "1" means "Negative outcome for Fannie Mae"
---
#### This Notebook:
* Input required: a file that is label-encoded and ready for machine learning
* Outputs generated: CSV file that is ready for PyCaret setup()

#### Expected Workflow
1. Scott - Data Pre - 1 - Feature EEE
2. Scott - Data Pre - 2 - 50 50 split train test
3. Scott - Model - 1- PyCaret Setup and Create Model
4. Scott - Predict - 1 - Holdout Data

In [26]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
#!pip install pycaret
from pycaret.classification import *
#from pycaret.regression import *

from sklearn.feature_selection import VarianceThreshold

import winsound

# Tell Jupyter to display all text, not just "the last" and print()
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'

%pwd

def DoneNotice(duration_ms = 1000):
    duration = duration_ms  # milliseconds
    freq = 440  #Hz
    winsound.Beep(freq, duration)

from IPython.display import Markdown, display
def Important(html_tag, message, color):
    colorstr = f"<{html_tag} style='color:{color}'>{message}</{html_tag}>"
    display(Markdown(colorstr))

'C:\\Users\\Scott\\Desktop\\Project3_2\\Scott\\ML EDA'

# Importing the data

In [27]:
dforig = pd.read_csv("../data/MLReady/FM_FULL_EPOCH2_MLReady.csv")
df = dforig.copy()
df.head()

DoneNotice(100)

Important("h1", "Full dataset loaded into `df`", 'blue')
rows, cols = df.shape
print(f'Full dataset has {rows:,} rows with {cols:,} columns/features')

print(f'Epoch 2: {df.origYear.unique().tolist()}')
print(df.shape)

Unnamed: 0  origChannel  origIntRate  origUPB  origLTV  numBorrowers  \
0           0            2        5.125   348000       87             1   
1           1            3        4.625   195000       52             2   
2           2            2        4.875   342000       80             1   
3           3            1        5.375    93000       70             1   
4           4            1        4.875   182000       76             2   

   origDebtIncRatio  borrCreditScore  loanPurp  zipCode  ...  \
0                50              689         2       51  ...   
1                54              703         1       82  ...   
2                54              746         1      981  ...   
3                50              780         1      496  ...   
4                22              802         1       18  ...   

   fmacRateVolatility  fredRate  rateDiffAbove  rateDiffBelow  rateDiffAvg  \
0            0.041667      2.87         -0.125         -0.085       -0.005   
1            0.041667      2.87         -0.625          0.415       -0.505   
2            0.041667      2.87         -0.375          0.165       -0.255   
3            0.041667      2.87          0.125         -0.335        0.245   
4            0.041667      2.87         -0.375          0.165       -0.255   

   rateDiffAbovePct  rateDiffBelowPct  rateDiffAvgPct  origYear  origMonth  
0         -0.023810         -0.016865       -0.000975      2009          2  
1         -0.119048          0.082341       -0.098441      2009          2  
2         -0.071429          0.032738       -0.049708      2009          2  
3          0.023810         -0.066468        0.047758      2009          2  
4         -0.071429          0.032738       -0.049708      2009          2  

[5 rows x 32 columns]

<h1 style='color:blue'>Full dataset loaded into `df`</h1>

Full dataset has 119,696 rows with 32 columns/features
Epoch 2: [2009, 2010, 2011, 2012, 2013]
(119696, 32)


In [28]:
# Get the data into the data types you want:
df = df.astype({
    'origLTV':'int'
    , 'numBorrowers':'int'
    , 'origDebtIncRatio':'int'
    , 'borrCreditScore':'int'
    , 'mortInsType':'int'
    , 'bestCreditScore':'int'
    , 'worstCreditScore':'int'
    , 'avgCreditScore':'int'
    , 'zeroBalCode':'object'}
)

# Pre-Processing: Feature Elimination

Remove each features' dataseries and remove features that:
* Step 1: Run a Pandas Profiling Report
* Step 2: Remove the index
* Step 3: Evaluate whether rows have zero to low variance
* Step 4: Are not part of a either a "closed" event (sale/closed/defaulted/etc)
* Step 5: Any unique identifiers that are not helpful in predicting the target

### Step 1: Run a Pandas Profiling Report

In [4]:
df.head()

Unnamed: 0  origChannel  origIntRate  origUPB  origLTV  numBorrowers  \
0           0            2        5.125   348000       87             1   
1           1            3        4.625   195000       52             2   
2           2            2        4.875   342000       80             1   
3           3            1        5.375    93000       70             1   
4           4            1        4.875   182000       76             2   

   origDebtIncRatio  borrCreditScore  loanPurp  zipCode  ...  \
0                50              689         2       51  ...   
1                54              703         1       82  ...   
2                54              746         1      981  ...   
3                50              780         1      496  ...   
4                22              802         1       18  ...   

   fmacRateVolatility  fredRate  rateDiffAbove  rateDiffBelow  rateDiffAvg  \
0            0.041667      2.87         -0.125         -0.085       -0.005   
1            0.041667      2.87         -0.625          0.415       -0.505   
2            0.041667      2.87         -0.375          0.165       -0.255   
3            0.041667      2.87          0.125         -0.335        0.245   
4            0.041667      2.87         -0.375          0.165       -0.255   

   rateDiffAbovePct  rateDiffBelowPct  rateDiffAvgPct origYear  origMonth  
0         -0.023810         -0.016865       -0.000975     2009          2  
1         -0.119048          0.082341       -0.098441     2009          2  
2         -0.071429          0.032738       -0.049708     2009          2  
3          0.023810         -0.066468        0.047758     2009          2  
4         -0.071429          0.032738       -0.049708     2009          2  

[5 rows x 32 columns]

In [5]:
from pandas_profiling import ProfileReport

profile = ProfileReport(df, title="Pandas Profiling Report - Before")

In [6]:
profile

### Step 2: Remove the index

In [14]:
df.head()

Unnamed: 0  origChannel  origIntRate  origUPB  origLTV  numBorrowers  \
0           0            2        5.125   348000       87             1   
1           1            3        4.625   195000       52             2   
2           2            2        4.875   342000       80             1   
3           3            1        5.375    93000       70             1   
4           4            1        4.875   182000       76             2   

   origDebtIncRatio  borrCreditScore  loanPurp  zipCode  ...  \
0                50              689         2       51  ...   
1                54              703         1       82  ...   
2                54              746         1      981  ...   
3                50              780         1      496  ...   
4                22              802         1       18  ...   

   fmacRateVolatility  fredRate  rateDiffAbove  rateDiffBelow  rateDiffAvg  \
0            0.041667      2.87         -0.125         -0.085       -0.005   
1            0.041667      2.87         -0.625          0.415       -0.505   
2            0.041667      2.87         -0.375          0.165       -0.255   
3            0.041667      2.87          0.125         -0.335        0.245   
4            0.041667      2.87         -0.375          0.165       -0.255   

   rateDiffAbovePct  rateDiffBelowPct  rateDiffAvgPct origYear  origMonth  
0         -0.023810         -0.016865       -0.000975     2009          2  
1         -0.119048          0.082341       -0.098441     2009          2  
2         -0.071429          0.032738       -0.049708     2009          2  
3          0.023810         -0.066468        0.047758     2009          2  
4         -0.071429          0.032738       -0.049708     2009          2  

[5 rows x 32 columns]

In [29]:
# Remove the previous index column
df.drop(['Unnamed: 0'], 1, inplace=True)

# Pandas changes it to "Unnamed_0"
# df.drop(['Unnamed_0'], 1, inplace=True)

### Step 3: Evaluate whether rows have zero to low variance

In [30]:
X = df.loc[:, df.columns != 'zeroBalCode']
y = df['zeroBalCode']

rows, cols = X.shape
print(f'There are currently {cols} features and {rows} rows')
print(type(X))

There are currently 30 features and 119696 rows
<class 'pandas.core.frame.DataFrame'>


In [31]:
dfOptimized = df.copy()

# origChannel ?

dfOptimized.drop([
        # Not used in the application process:
        'borrCreditScore'
        , 'bestCreditScore'
        , 'avgCreditScore'
    
        # These features introduce collinearity problems:
        , 'rateDiffAbove'
        , 'rateDiffBelow'
        , 'rateDiffAvg'
        , 'rateDiffBelowPct'
        , 'rateDiffAvgPct'
        , 'fmacRateMax'
        , 'fmacRateMin'
        , 'fmacRateAvg'
        , 'fmacRateVolatility'
        , 'fredRate'
    
        # Derived from a derived column:
        , 'rateDiffAbovePct'
    
        # Not complete:
        , 'zipCode'
    
        # Guess
        , 'pMIperct'
        , 'origMonth'
    ]
    , axis=1
    , inplace=True
)

dfOptimized.head()

origChannel  origIntRate  origUPB  origLTV  numBorrowers  origDebtIncRatio  \
0            2        5.125   348000       87             1                50   
1            3        4.625   195000       52             2                54   
2            2        4.875   342000       80             1                54   
3            1        5.375    93000       70             1                50   
4            1        4.875   182000       76             2                22   

   loanPurp  mortInsType  worstCreditScore  bankNumber  stateNumber    mSA  \
0         2            1               689          80           49      0   
1         1            0               703           4           32  12100   
2         1            0               746           3           50  42660   
3         1            0               780          54           23      0   
4         1            0               776          45           20  14460   

  zeroBalCode  origYear  
0           1      2009  
1           0      2009  
2           0      2009  
3           1      2009  
4           0      2009

In [32]:
# Drop all except 2011 and 2012
dfOptimized['origYear'].value_counts()

dfOptimized = dfOptimized[
    (dfOptimized['origYear'] == 2010) 
    | (dfOptimized['origYear'] == 2011)
    | (dfOptimized['origYear'] == 2012)
].copy()

dfOptimized['origYear'].value_counts()
dfOptimized.head()

2009    53126
2010    24040
2012    19195
2011    14976
2013     8359
Name: origYear, dtype: int64

2010    24040
2012    19195
2011    14976
Name: origYear, dtype: int64

origChannel  origIntRate  origUPB  origLTV  numBorrowers  \
53126            2        4.990   346000       44             2   
53127            1        4.875    96000       44             1   
53128            3        4.875   159000       68             1   
53129            2        4.875   130000       47             2   
53130            1        5.500   107000       55             1   

       origDebtIncRatio  loanPurp  mortInsType  worstCreditScore  bankNumber  \
53126                39         2            0               820          27   
53127                33         1            0               750          80   
53128                21         1            0               761           4   
53129                28         1            0               773          57   
53130                31         1            0               599          45   

       stateNumber    mSA zeroBalCode  origYear  
53126            4  41940           0      2010  
53127           47  47260           1      2010  
53128           50  42660           0      2010  
53129            1  19460           0      2010  
53130            6  35980           0      2010

# Encoding

Label encoding is converting categoricals (like "Texas") to a static number (30), in which you can later perform a lookup

One-hot encoding is better when you have dichotomous *Yes/No* and it will make columns for those. 

Rule of thumb: Use label encoding when you have a large # of distinct values in your categorical feature, and use one-hot encoding when you have a small # of distinct values

In [33]:
# What is the variance?
import statistics as stat
for c in dfOptimized.columns.tolist():
    varianceNb = stat.variance(dfOptimized[c])
    print(f'{c}: {varianceNb}')

origChannel: 0.8881716721824773
origIntRate: 0.32132015569676087
origUPB: 17207012231.266636
origLTV: 245.07734515010733
numBorrowers: 0.25267657116127107
origDebtIncRatio: 82.75495275082461
loanPurp: 0.24985048454028694
mortInsType: 0.11482130252763531
worstCreditScore: 2365.498753320352
bankNumber: 496.8700702945107
stateNumber: 258.6280638063228
mSA: 211575218.90900737
zeroBalCode: 0.10401349513608728
origYear: 0.7358141634457195


# Assumptions
1. Assumption 1: Fannie Mae states that they do not buy "jumbo loans" (identified as > $450,000 original loan). However, the data set does have some of those

1. Assumption 2: loanPurp has 1 record in Epoch 2 - removing all `loanPurp == 3`

1. Assumption 3: numBorrowers has only 158 rows w 3 borrowers - removing all `numBorrowers > 2`

1. Assumption 4: mortInsType has lender borrowed and investor borrowed - remove those, then drop feature`


In [34]:
# Assumption 1: Drop any loans with an Unpaid Balance upon acquire > $417,000
rows, cols = dfOptimized.shape
print('#############################################')
print('Assumption 1: Remove jumbo loans')
print(f'   - Before removing: {rows}')

dfAssumption1 = dfOptimized[dfOptimized['origUPB'] < 417000].copy()
rows2, cols2 = dfAssumption1.shape
print(f'   - After removing: {rows2}')
print(f'   - Net removed: {rows - rows2}')
print('#############################################')

#############################################
Assumption 1: Remove jumbo loans
   - Before removing: 58211
   - After removing: 53038
   - Net removed: 5173
#############################################


In [35]:
# Assumption 2: Assumption 2: loanPurp has 1 record in Epoch 2 - removing all loanPurp == 3
rows, cols = dfAssumption1.shape
print('#############################################')
print('Assumption 2: Remove loan purpose "3"')
print(f'   - Before removing: {rows}')

dfAssumption2 = dfAssumption1[dfAssumption1['loanPurp'] <= 2].copy()
rows2, cols2 = dfAssumption2.shape
print(f'   - After removing: {rows2}')
print(f'   - Net removed: {rows - rows2}')
print('#############################################')

#############################################
Assumption 2: Remove loan purpose "3"
   - Before removing: 53038
   - After removing: 53037
   - Net removed: 1
#############################################


In [36]:
# Assumption 3: numBorrowers has only 158 rows w 3 borrowers - removing all numBorrowers > 2
dfAssumption2['numBorrowers'].value_counts()

1    29896
2    23059
3       72
4       10
Name: numBorrowers, dtype: int64

In [37]:
rows, cols = dfAssumption2.shape
print('#############################################')
print('Assumption 2: Removing all numBorrowers > 2')
print(f'   - Before removing: {rows}')

dfAssumption3 = dfAssumption2[dfAssumption2['numBorrowers'] <= 2].copy()
rows2, cols2 = dfAssumption3.shape
print(f'   - After removing: {rows2}')
print(f'   - Net removed: {rows - rows2}')
print('#############################################')

#############################################
Assumption 2: Removing all numBorrowers > 2
   - Before removing: 53037
   - After removing: 52955
   - Net removed: 82
#############################################


In [38]:
dfOptimized['mortInsType'].value_counts()

0    52409
1     5279
2      523
Name: mortInsType, dtype: int64

In [39]:
# Assumption 4: mortInsType has lender borrowed and investor borrowed - remove those`
rows, cols = dfAssumption3.shape
print('#############################################')
print('Assumption 4: Remove non-borrower loans')
print(f'   - Before removing: {rows}')

dfAssumption4 = dfAssumption3[dfAssumption3['mortInsType'] == 0].copy()
rows2, cols2 = dfAssumption4.shape
print(f'   - After removing: {rows2}')
print(f'   - Net removed: {rows - rows2}')
print('#############################################')

# Drop the feature
dfAssumption4.drop(['mortInsType'], axis=1, inplace=True)

#############################################
Assumption 4: Remove non-borrower loans
   - Before removing: 52955
   - After removing: 47313
   - Net removed: 5642
#############################################


In [40]:
dfAssumption4.head()

origChannel  origIntRate  origUPB  origLTV  numBorrowers  \
53126            2        4.990   346000       44             2   
53127            1        4.875    96000       44             1   
53128            3        4.875   159000       68             1   
53129            2        4.875   130000       47             2   
53130            1        5.500   107000       55             1   

       origDebtIncRatio  loanPurp  worstCreditScore  bankNumber  stateNumber  \
53126                39         2               820          27            4   
53127                33         1               750          80           47   
53128                21         1               761           4           50   
53129                28         1               773          57            1   
53130                31         1               599          45            6   

         mSA zeroBalCode  origYear  
53126  41940           0      2010  
53127  47260           1      2010  
53128  42660           0      2010  
53129  19460           0      2010  
53130  35980           0      2010

In [41]:
dfAssumption4.dtypes

origChannel           int64
origIntRate         float64
origUPB               int64
origLTV               int32
numBorrowers          int32
origDebtIncRatio      int32
loanPurp              int64
worstCreditScore      int32
bankNumber            int64
stateNumber           int64
mSA                   int64
zeroBalCode          object
origYear              int64
dtype: object

In [42]:
dfAssumption4.to_csv(r'../data/DataPre-01-Feature-EEE-2010-2012.csv')

In [43]:
print('#############################################')
rows3, cols3 = dfOptimized.shape
print(f'Original dataframe: {rows3} rows and {cols3} columns')

rows4, cols4 = dfAssumption4.shape
print(f'Final dataframe:    {rows4} rows and {cols4} columns')
print('#############################################')

#############################################
Original dataframe: 58211 rows and 14 columns
Final dataframe:    47313 rows and 13 columns
#############################################


In [44]:
export = dfAssumption4[dfAssumption4['origYear'] == 2010].copy()
export.drop('origYear', axis = 1, inplace=True)
export.to_csv(r'../data/DataPre-01-Feature-EEE-2010.csv')

In [45]:
export = dfAssumption4[dfAssumption4['origYear'] == 2011].copy()
export.drop('origYear', axis = 1, inplace=True)
export.to_csv(r'../data/DataPre-01-Feature-EEE-2011.csv')

In [46]:
export = dfAssumption4[dfAssumption4['origYear'] == 2012].copy()
export.drop('origYear', axis = 1, inplace=True)
export.to_csv(r'../data/DataPre-01-Feature-EEE-2012.csv')